# Overview

**GENERAL THOUGHTS:**
Use AutoML (AutoGluon.Tabular) as a general way to investigate which algorithm, pre-processing, feature engineering options are (well) suited for the given tasks, as well as to investigate the potential performance based on a (large) varity of configurations of those options.
The notebook includes multiple scenarios of using AutoML:
- including and excluding custom data pre-processing (see below)
- including auto pre-processing by AutoGluon.Tabular
- including auto feature engineering by AutoGluon.Tabular
https://auto.gluon.ai/stable/tutorials/tabular/tabular-feature-engineering.html
- including multiple classifiers by using:
  - multiple ml algorithms
  - "standard" HPO for each algorithm defined by AutoGluon.Tabular
  - ensables for algorithms (bagging and stacking)

**DATA PREPROCESSING:**

Imbalanced data:
- over_sampling for imbalanced data
- cost-sensitive learning for imbalanced data

categorical data:
- Ordinal Data: The categories have an inherent order
- Nominal Data: The categories do not have an inherent order



**MULTI-CLASS CLASSIFIERS:**
- Overview of models to be considered using AutoML (AutoGluon.Tabular):  
  - [X] RandomForest
  - [X] ExtraTrees
  - [X] XGBoost
  - [X] LightGBM
  - [X] KNeughbors
  - [X] CatBoost

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

import mlflow

import os
from datetime import datetime
import yaml
import json

In [2]:
import sklearn
from sklearn.pipeline import Pipeline, make_pipeline
from sklearn.compose import ColumnTransformer
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_validate
from sklearn.model_selection import cross_val_score
# from sklearn.model_selection import GridSearchCV
# from sklearn.experimental import enable_halving_search_cv
# from sklearn.model_selection import HalvingGridSearchCV, HalvingRandomSearchCV
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import LabelEncoder, OrdinalEncoder, OneHotEncoder, MinMaxScaler, StandardScaler
from sklearn.preprocessing import PowerTransformer
from sklearn.metrics import confusion_matrix
from sklearn.metrics import ConfusionMatrixDisplay
from sklearn.metrics import f1_score, precision_score, recall_score, roc_auc_score
from sklearn.metrics import classification_report
from sklearn.utils import class_weight
from sklearn.utils.class_weight import compute_sample_weight

# from sklearn.dummy import DummyClassifier
# from sklearn.base import BaseEstimator, ClassifierMixin

# from sklearn.tree import DecisionTreeClassifier
# from sklearn.ensemble import RandomForestClassifier
# import xgboost as xgb
# import lightgbm as lgbm

import optuna
# from optuna.samplers import TPESampler

import imblearn
from imblearn.over_sampling import RandomOverSampler

from scipy.stats import randint as sp_randint
from scipy.stats import uniform as sp_uniform


/Users/dat/miniconda3/envs/py_ml_packaging_classification/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
from autogluon.tabular import TabularDataset, TabularPredictor

In [4]:
SEED = 42

clf_name = "dt_clf"

# Get current date and time
now = datetime.now()
# Format date and time
formatted_date_time = now.strftime("%Y-%m-%d_%H:%M:%S")
print(formatted_date_time)

2024-01-18_18:44:27


# Load and prepare data

In [5]:
df = pd.read_csv('../../data/output/df_ml.csv', sep='\t')

df['material_number'] = df['material_number'].astype('object')

df_sub = df[[
    'material_number',
    'brand',
    'product_area',
    'core_segment',
    'component',
    'manufactoring_location',
    'characteristic_value',
    'material_weight', 
    'packaging_code',
    'packaging_category',
]]

# AutoML: without custom pre-processing; restricted selection of models including HPO and model ensembling

## Split data into train and test

In [6]:
# Define features and target
X = df_sub.iloc[:, :-1]
y = df_sub.iloc[:, -1]  # the last column is the target

In [7]:
# Generate train/test sets
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, stratify=y,
    random_state=SEED
)

## Transform to AutoML data format

In [8]:
df_train = pd.concat([X_train, y_train], axis=1)

In [9]:
train_data = TabularDataset(df_train)

## AutoML training pipeline

In [11]:
label = 'packaging_category'
automl_predictor = TabularPredictor(
    label=label,
    problem_type='multiclass',
    eval_metric='f1_macro',
    sample_weight='balance_weight'
).fit(
    train_data=train_data,
    tuning_data=None, # If tuning_data = None, fit() will automatically hold out some random validation examples from train_data.
    holdout_frac=0.2, # Default value (if None) is selected based on the number of rows in the training data.
    time_limit=60*60,
    presets=['best_quality'], # default = ['medium_quality'], any user-specified arguments in fit() will override the values used by presets.
    # auto_stack=False, # Whether AutoGluon should automatically utilize bagging and multi-layer stack ensembling to boost predictive accuracy.
    # included_model_types=[],
    # excluded_model_types=['FASTAI', 'AG_AUTOMM'],
    hyperparameter_tune_kwargs = {  # HPO is not performed unless hyperparameter_tune_kwargs is specified. Searchspaces are provided for some models, but not for all. Where no searchspace is provided, a fixed set of hyper-parameters is defined. (see /searchspace under each model: https://github.com/autogluon/autogluon/tree/master/tabular/src/autogluon/tabular/models).
        # 'num_trials': 15, # try at most n different hyperparameter configurations for each type of model
        'scheduler' : 'local',
        'searcher': 'auto', # ‘auto’: Perform bayesian optimization search on NN_TORCH and FASTAI models. Perform random search on other models.
    }  # Refer to TabularPredictor.fit docstring for all valid values
)

No path specified. Models will be saved in: "AutogluonModels/ag-20240118_174517"
Presets specified: ['best_quality']
Stack configuration (auto_stack=True): num_stack_levels=1, num_bag_folds=8, num_bag_sets=1
Dynamic stacking is enabled (dynamic_stacking=True). AutoGluon will try to determine whether the input data is affected by stacked overfitting and enable or disable stacking as a consequence.
Detecting stacked overfitting by sub-fitting AutoGluon on the input data. That is, copies of AutoGluon will be sub-fit on subset(s) of the data. Then, the holdout validation data is used to detect stacked overfitting.
Sub-fit(s) time limit is: 60 seconds.
Starting holdout-based sub-fit for dynamic stacking. Context path is: AutogluonModels/ag-20240118_174517/ds_sub_fit/sub_fit_ho.
Using predefined sample weighting strategy: balance_weight. Evaluation metrics will ignore sample weights, specify weight_evaluation=True to instead report weighted metrics.
Beginning AutoGluon training ... Time limi

In [12]:
# Evaluation of models on training data
automl_predictor.leaderboard()

model  score_val eval_metric  pred_time_val   fit_time  \
0  KNeighborsDist_BAG_L1   0.093594    f1_macro       0.002528   0.299576   
1    WeightedEnsemble_L2   0.093594    f1_macro       0.023991  11.141783   
2    WeightedEnsemble_L3   0.093594    f1_macro       0.024210  11.221712   
3  KNeighborsUnif_BAG_L1   0.089275    f1_macro       0.001786   0.280633   

   pred_time_val_marginal  fit_time_marginal  stack_level  can_infer  \
0                0.002528           0.299576            1       True   
1                0.021463          10.842207            2       True   
2                0.021682          10.922136            3       True   
3                0.001786           0.280633            1       True   

   fit_order  
0          2  
1          3  
2          4  
3          1

In [14]:
# Evaluation of models on test data
df_test = pd.concat([X_test, y_test], axis=1)
test_data = TabularDataset(df_test)

automl_predictor.leaderboard(test_data)

model  score_test  score_val eval_metric  pred_time_test  \
0  KNeighborsDist_BAG_L1    0.188669   0.093594    f1_macro        0.067607   
1    WeightedEnsemble_L3    0.188669   0.093594    f1_macro        0.069288   
2    WeightedEnsemble_L2    0.188669   0.093594    f1_macro        0.069789   
3  KNeighborsUnif_BAG_L1    0.181568   0.089275    f1_macro        0.056656   

   pred_time_val   fit_time  pred_time_test_marginal  pred_time_val_marginal  \
0       0.002528   0.299576                 0.067607                0.002528   
1       0.024210  11.221712                 0.001681                0.021682   
2       0.023991  11.141783                 0.002182                0.021463   
3       0.001786   0.280633                 0.056656                0.001786   

   fit_time_marginal  stack_level  can_infer  fit_order  
0           0.299576            1       True          2  
1          10.922136            3       True          4  
2          10.842207            2       True          3  
3           0.280633            1       True          1

In [15]:
# For a single specified model: make predictions and perform detailed evaluation on hold out test data
i = 3  # index of model to use
model_to_use = automl_predictor.model_names()[i]
preds_y_test = automl_predictor.predict(X_test, model=model_to_use)
print("Predictions:  ", list(preds_y_test)[:5])

print(classification_report(y_test, preds_y_test))

Predictions:   ['Blister and Insert Card', 'Corrugated carton', 'Blister and Insert Card', 'Blister and Insert Card', 'Corrugated carton']
                            precision    recall  f1-score   support

   Blister and Insert Card       0.16      0.93      0.28      1749
  Blister and sealed blist       0.39      0.30      0.34      1582
            Book packaging       0.00      0.00      0.00         2
Cardb. Sleeve w - w/o Shr.       0.04      0.24      0.06       135
  Cardboard hanger w/o bag       0.94      0.19      0.31        80
    Carton cover (Lid box)       0.23      0.23      0.23       130
   Carton tube with or w/o       0.00      0.00      0.00         9
                      Case       0.13      0.16      0.15        97
         Corrugated carton       0.49      0.53      0.51       774
        Countertop display       0.14      0.07      0.09        30
                  Envelope       0.80      0.27      0.41        59
          Fabric packaging       0.00      0

/Users/dat/miniconda3/envs/py_ml_packaging_classification/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1471: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/dat/miniconda3/envs/py_ml_packaging_classification/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1471: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/dat/miniconda3/envs/py_ml_packaging_classification/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1471: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to c

# AutoML: custom pre-processing; restricted selection of models including HPO and model ensembling

## Define features and target, performe oversampling, split data into train and test

In [ ]:
# Define features and target
X = df_sub.iloc[:, :-1]
y = df_sub.iloc[:, -1]  # the last column is the target

In [ ]:
distribution_classes = y.value_counts()
print('Class distribution before oversmapling')
print(distribution_classes.to_dict())

# NOTE: Oversampling so each class has at least 100 sample; to properly apply CV and evaluation
dict_oversmapling = {
    'Metal Cassette': 100,
    'Carton tube with or w/o': 100,
    'Wooden box': 100,
    'Fabric packaging': 100,
    'Book packaging': 100
}
# define oversampling strategy
oversampler = RandomOverSampler(sampling_strategy=dict_oversmapling, random_state=SEED)
# fit and apply the transform
X_oversample, y_oversample = oversampler.fit_resample(X, y)

distribution_classes = y_oversample.value_counts()
print('\n')
print('Class distribution after oversmapling')
print(distribution_classes.to_dict())

Class distribution before oversmapling
{'Hanger/ Clip': 13543, 'Tube': 11687, 'Blister and Insert Card': 8744, 'TightPack': 8296, 'Folding carton': 8219, 'Blister and sealed blist': 7912, 'Corrugated carton': 3872, 'Paperboard pouch': 3478, 'Trap Folding Card': 2188, 'Plastic Pouch': 1904, 'Plastic bag with header': 1850, 'Plastic Cassette': 1708, 'Shrink film and insert o': 1499, 'Plastic Box': 1491, 'Unpacked': 1415, 'Skincard': 1143, 'Trap Card': 804, 'Cardb. Sleeve w - w/o Shr.': 676, 'Carton cover (Lid box)': 652, 'Case': 485, 'Tray Packer': 431, 'Cardboard hanger w/o bag': 400, 'Envelope': 295, 'Countertop display': 150, 'Metal Cassette': 50, 'Carton tube with or w/o': 44, 'Wooden box': 16, 'Fabric packaging': 15, 'Book packaging': 10}




Class distribution after oversmapling
{'Hanger/ Clip': 13543, 'Tube': 11687, 'Blister and Insert Card': 8744, 'TightPack': 8296, 'Folding carton': 8219, 'Blister and sealed blist': 7912, 'Corrugated carton': 3872, 'Paperboard pouch': 3478, 'Trap Folding Card': 2188, 'Plastic Pouch': 1904, 'Plastic bag with header': 1850, 'Plastic Cassette': 1708, 'Shrink film and insert o': 1499, 'Plastic Box': 1491, 'Unpacked': 1415, 'Skincard': 1143, 'Trap Card': 804, 'Cardb. Sleeve w - w/o Shr.': 676, 'Carton cover (Lid box)': 652, 'Case': 485, 'Tray Packer': 431, 'Cardboard hanger w/o bag': 400, 'Envelope': 295, 'Countertop display': 150, 'Carton tube with or w/o': 100, 'Wooden box': 100, 'Metal Cassette': 100, 'Book packaging': 100, 'Fabric packaging': 100}


In [ ]:
# Generate train/test sets
X_train, X_test, y_train, y_test = train_test_split(
    X_oversample, y_oversample, test_size=0.2, stratify=y_oversample,
    random_state=SEED
)

In [9]:
# DEFINE & EXECUTE PIPELINE

# define feature processing pipeline
# define numerical feature processing
numerical_features = X_train.select_dtypes(include='number').columns.tolist()
# print(f'There are {len(numerical_features)} numerical features:', '\n')
# print(numerical_features)
numeric_feature_pipeline = Pipeline(steps=[
    ('impute', SimpleImputer(strategy='median')),
    ('log_transform', PowerTransformer()),
    # ('scale', MinMaxScaler())
])
# define categorical feature processing
categorical_features = X_train.select_dtypes(exclude='number').columns.tolist()
# print(f'There are {len(categorical_features)} categorical features:', '\n')
# print(categorical_features)
categorical_feature_pipeline = Pipeline(steps=[
    ('impute', SimpleImputer(strategy='most_frequent')),
    ('ordinal', OrdinalEncoder(handle_unknown='use_encoded_value', unknown_value=np.nan)),
    # ('one_hot', OneHotEncoder(handle_unknown='ignore', max_categories=None, sparse=False))
])
# apply both pipeline on seperate columns using "ColumnTransformer"
preprocess_pipeline = ColumnTransformer(transformers=[
    ('number', numeric_feature_pipeline, numerical_features),
    ('category', categorical_feature_pipeline, categorical_features)
]).set_output(transform="pandas")
X_train_transformed = preprocess_pipeline.fit_transform(X_train)

# encode target variable
label_encoder = LabelEncoder()
y_train_transformed = label_encoder.fit_transform(y_train)
y_train_transformed = pd.Series(data=y_train_transformed, index=y_train.index, name=y_train.name)

## Transform to AutoML data format

In [10]:
df_train = pd.concat([X_train_transformed, y_train_transformed], axis=1)

In [11]:
train_data = TabularDataset(df_train)

## AutoML training pipeline

In [12]:
label = 'packaging_category'
automl_predictor = TabularPredictor(
    label=label,
    problem_type='multiclass',
    eval_metric='f1_macro',
    sample_weight='balance_weight'
).fit(
    train_data=train_data,
    tuning_data=None, # If tuning_data = None, fit() will automatically hold out some random validation examples from train_data.
    holdout_frac=0.2, # Default value (if None) is selected based on the number of rows in the training data.
    time_limit=60*60,
    presets=['best_quality'], # default = ['medium_quality'], any user-specified arguments in fit() will override the values used by presets.
    # auto_stack=False, # Whether AutoGluon should automatically utilize bagging and multi-layer stack ensembling to boost predictive accuracy.
    # included_model_types=[],
    # excluded_model_types=['FASTAI', 'AG_AUTOMM'],
    hyperparameter_tune_kwargs = {  # HPO is not performed unless hyperparameter_tune_kwargs is specified. Searchspaces are provided for some models, but not for all. Where no searchspace is provided, a fixed set of hyper-parameters is defined. (see /searchspace under each model: https://github.com/autogluon/autogluon/tree/master/tabular/src/autogluon/tabular/models).
        # 'num_trials': 15, # try at most n different hyperparameter configurations for each type of model
        'scheduler' : 'local',
        'searcher': 'auto', # ‘auto’: Perform bayesian optimization search on NN_TORCH and FASTAI models. Perform random search on other models.
    }  # Refer to TabularPredictor.fit docstring for all valid values
)

No path specified. Models will be saved in: "AutogluonModels/ag-20240118_160631"
Presets specified: ['best_quality']
Stack configuration (auto_stack=True): num_stack_levels=1, num_bag_folds=8, num_bag_sets=1
Dynamic stacking is enabled (dynamic_stacking=True). AutoGluon will try to determine whether the input data is affected by stacked overfitting and enable or disable stacking as a consequence.
Detecting stacked overfitting by sub-fitting AutoGluon on the input data. That is, copies of AutoGluon will be sub-fit on subset(s) of the data. Then, the holdout validation data is used to detect stacked overfitting.
Sub-fit(s) time limit is: 3600 seconds.
Starting holdout-based sub-fit for dynamic stacking. Context path is: AutogluonModels/ag-20240118_160631/ds_sub_fit/sub_fit_ho.
Using predefined sample weighting strategy: balance_weight. Evaluation metrics will ignore sample weights, specify weight_evaluation=True to instead report weighted metrics.
Beginning AutoGluon training ... Time li

In [13]:
# Evaluation of models on training data
automl_predictor.leaderboard()

model  score_val eval_metric  pred_time_val  \
0        WeightedEnsemble_L2   0.791491    f1_macro       0.110476   
1        WeightedEnsemble_L3   0.791491    f1_macro       0.111575   
2    RandomForestGini_BAG_L1   0.782605    f1_macro       0.002573   
3     ExtraTrees_r197_BAG_L1   0.781980    f1_macro       0.003979   
4   RandomForest_r166_BAG_L1   0.781682    f1_macro       0.002812   
5    RandomForestEntr_BAG_L1   0.781401    f1_macro       0.004407   
6      ExtraTrees_r42_BAG_L1   0.781042    f1_macro       0.004615   
7    RandomForest_r16_BAG_L1   0.780871    f1_macro       0.004010   
8   RandomForest_r195_BAG_L1   0.780347    f1_macro       0.003703   
9      ExtraTreesGini_BAG_L1   0.778449    f1_macro       0.003007   
10     ExtraTrees_r49_BAG_L1   0.777724    f1_macro       0.005675   
11     ExtraTreesEntr_BAG_L1   0.777352    f1_macro       0.003352   
12   RandomForest_r39_BAG_L1   0.766269    f1_macro       0.002889   
13   RandomForest_r15_BAG_L1   0.751390    f1_macro       0.003758   
14  RandomForest_r127_BAG_L1   0.718694    f1_macro       0.002473   
15    ExtraTrees_r126_BAG_L1   0.701233    f1_macro       0.002427   
16    ExtraTrees_r172_BAG_L1   0.690067    f1_macro       0.003647   
17    ExtraTrees_r178_BAG_L1   0.669929    f1_macro       0.004077   
18        XGBoost_r33_BAG_L1   0.624382    f1_macro       0.005011   
19       XGBoost_r194_BAG_L1   0.603200    f1_macro       0.003779   
20        XGBoost_r34_BAG_L1   0.591134    f1_macro       0.003568   
21        XGBoost_r49_BAG_L1   0.582303    f1_macro       0.005934   
22        XGBoost_r98_BAG_L1   0.553192    f1_macro       0.003840   
23        XGBoost_r22_BAG_L1   0.548661    f1_macro       0.004371   
24      LightGBM_r131_BAG_L1   0.547810    f1_macro       0.004415   
25        LightGBM_BAG_L1/T1   0.540740    f1_macro       0.004555   
26      ExtraTrees_r4_BAG_L1   0.534383    f1_macro       0.004064   
27   RandomForest_r34_BAG_L1   0.524749    f1_macro       0.004727   
28        XGBoost_r89_BAG_L1   0.522281    f1_macro       0.003932   
29        XGBoost_r95_BAG_L1   0.516245    f1_macro       0.003606   
30       LightGBM_r15_BAG_L1   0.507396    f1_macro       0.006140   
31     KNeighborsDist_BAG_L1   0.474520    f1_macro       0.002409   
32        XGBoost_r31_BAG_L1   0.430014    f1_macro       0.005380   
33      CatBoost_r167_BAG_L1   0.403145    f1_macro       0.004060   
34      CatBoost_r143_BAG_L1   0.394502    f1_macro       0.005208   
35      CatBoost_r128_BAG_L1   0.387601    f1_macro       0.004529   
36        CatBoost_r9_BAG_L1   0.382033    f1_macro       0.003402   
37      CatBoost_r180_BAG_L1   0.379779    f1_macro       0.005697   
38       CatBoost_r86_BAG_L1   0.369906    f1_macro       0.008386   
39      CatBoost_r163_BAG_L1   0.369480    f1_macro       0.006520   
40       CatBoost_r70_BAG_L1   0.355340    f1_macro       0.004009   
41     KNeighborsUnif_BAG_L1   0.353719    f1_macro       0.004283   
42      CatBoost_r198_BAG_L1   0.350405    f1_macro       0.003687   
43        CatBoost_r6_BAG_L1   0.349586    f1_macro       0.003542   
44       CatBoost_r69_BAG_L1   0.346810    f1_macro       0.004425   
45       CatBoost_r60_BAG_L1   0.342508    f1_macro       0.003612   
46      CatBoost_r177_BAG_L1   0.340796    f1_macro       0.003644   
47       CatBoost_r12_BAG_L1   0.339138    f1_macro       0.005107   
48       CatBoost_r49_BAG_L1   0.335540    f1_macro       0.003515   
49      LightGBMXT_BAG_L1/T1   0.331468    f1_macro       0.005350   
50       CatBoost_r13_BAG_L1   0.330036    f1_macro       0.004353   
51        CatBoost_r5_BAG_L1   0.327651    f1_macro       0.003575   
52       CatBoost_r50_BAG_L1   0.319780    f1_macro       0.004293   
53      CatBoost_r137_BAG_L1   0.319624    f1_macro       0.005926   
54        CatBoost_BAG_L1/T1   0.289378    f1_macro       0.011681   
55       LightGBM_r94_BAG_L1   0.229184    f1_macro       0.004374   
56       LightGBM_r96_BAG_L1   0.

In [14]:
# Evaluation of models on test data

# process X_test for evaluation and predictions
X_test_transformed = preprocess_pipeline.transform(X_test)

# evaluate models on test data
y_test_transformed = label_encoder.transform(y_test)
y_test_transformed = pd.Series(data=y_test_transformed, index=y_test.index, name=y_test.name)
df_test = pd.concat([X_test_transformed, y_test_transformed], axis=1)
test_data = TabularDataset(df_test)

automl_predictor.leaderboard(test_data)

model  score_test  score_val eval_metric  \
0     ExtraTrees_r197_BAG_L1    0.753237   0.781980    f1_macro   
1        WeightedEnsemble_L3    0.750393   0.791491    f1_macro   
2        WeightedEnsemble_L2    0.750393   0.791491    f1_macro   
3      ExtraTrees_r42_BAG_L1    0.748384   0.781042    f1_macro   
4      ExtraTrees_r49_BAG_L1    0.741533   0.777724    f1_macro   
5      ExtraTreesGini_BAG_L1    0.740493   0.778449    f1_macro   
6      ExtraTreesEntr_BAG_L1    0.739568   0.777352    f1_macro   
7    RandomForestEntr_BAG_L1    0.727815   0.781401    f1_macro   
8   RandomForest_r166_BAG_L1    0.726957   0.781682    f1_macro   
9    RandomForestGini_BAG_L1    0.726926   0.782605    f1_macro   
10  RandomForest_r195_BAG_L1    0.720709   0.780347    f1_macro   
11   RandomForest_r16_BAG_L1    0.719355   0.780871    f1_macro   
12   RandomForest_r39_BAG_L1    0.708824   0.766269    f1_macro   
13   RandomForest_r15_BAG_L1    0.703859   0.751390    f1_macro   
14    ExtraTrees_r126_BAG_L1    0.687605   0.701233    f1_macro   
15    ExtraTrees_r172_BAG_L1    0.685124   0.690067    f1_macro   
16  RandomForest_r127_BAG_L1    0.683916   0.718694    f1_macro   
17    ExtraTrees_r178_BAG_L1    0.662413   0.669929    f1_macro   
18        XGBoost_r33_BAG_L1    0.609264   0.624382    f1_macro   
19       XGBoost_r194_BAG_L1    0.592794   0.603200    f1_macro   
20        XGBoost_r34_BAG_L1    0.585952   0.591134    f1_macro   
21        XGBoost_r49_BAG_L1    0.578487   0.582303    f1_macro   
22      LightGBM_r131_BAG_L1    0.553120   0.547810    f1_macro   
23        XGBoost_r98_BAG_L1    0.552192   0.553192    f1_macro   
24        XGBoost_r22_BAG_L1    0.536208   0.548661    f1_macro   
25        LightGBM_BAG_L1/T1    0.534781   0.540740    f1_macro   
26      ExtraTrees_r4_BAG_L1    0.525546   0.534383    f1_macro   
27        XGBoost_r89_BAG_L1    0.509577   0.522281    f1_macro   
28        XGBoost_r95_BAG_L1    0.501791   0.516245    f1_macro   
29   RandomForest_r34_BAG_L1    0.500262   0.524749    f1_macro   
30       LightGBM_r15_BAG_L1    0.497773   0.507396    f1_macro   
31     KNeighborsDist_BAG_L1    0.421719   0.474520    f1_macro   
32        XGBoost_r31_BAG_L1    0.416813   0.430014    f1_macro   
33      CatBoost_r167_BAG_L1    0.391213   0.403145    f1_macro   
34      LightGBMXT_BAG_L1/T1    0.385697   0.331468    f1_macro   
35      CatBoost_r128_BAG_L1    0.384071   0.387601    f1_macro   
36      CatBoost_r143_BAG_L1    0.381790   0.394502    f1_macro   
37        CatBoost_r9_BAG_L1    0.380563   0.382033    f1_macro   
38      CatBoost_r180_BAG_L1    0.380351   0.379779    f1_macro   
39       CatBoost_r86_BAG_L1    0.371692   0.369906    f1_macro   
40      CatBoost_r163_BAG_L1    0.366773   0.369480    f1_macro   
41       CatBoost_r70_BAG_L1    0.355664   0.355340    f1_macro   
42        CatBoost_r6_BAG_L1    0.347337   0.349586    f1_macro   
43      CatBoost_r198_BAG_L1    0.338615   0.350405    f1_macro   
44       CatBoost_r69_BAG_L1    0.337513   0.346810    f1_macro   
45       CatBoost_r60_BAG_L1    0.335617   0.342508    f1_macro   
46      CatBoost_r177_BAG_L1    0.331713   0.340796    f1_macro   
47       CatBoost_r12_BAG_L1    0.329600   0.339138    f1_macro   
48       CatBoost_r49_BAG_L1    0.327730   0.335540    f1_macro   
49       CatBoost_r13_BAG_L1    0.326058   0.330036    f1_macro   
50        CatBoost_r5_BAG_L1    0.324674   0.327651    f1_macro   
51       LightGBM_r94_BAG_L1    0.323277   0.229184    f1_macro   
52       CatBoost_r50_BAG_L1    0.322241   0.319780    f1_macro   
53     KNeighborsUnif_BAG_L1    0.320265   0.353719    f1_macro   
54      CatBoost_r137_BAG_L1    0.318984   0.319624    f1_macro   
55       LightGBM_r96_BAG_L1    0.310266   0.227400    f1_macro   
56        CatBoost_BAG_L1/T1    0.299009   0.289378    f1_macro   
57       LightGBM_r42_BAG_L1    0.268275   0.196376    f1_macro   

    pred_time_test  pred_time_val    fit_time  pred_time_test_margina

In [15]:
# For a single specified model: make predictions and perform detailed evaluation on hold out test data
i = 3  # index of model to use
model_to_use = automl_predictor.model_names()[i]
preds_y_test = automl_predictor.predict(X_test_transformed, model=model_to_use)
print("Predictions:  ", list(preds_y_test)[:5])

preds_y_test_inverse = label_encoder.inverse_transform(preds_y_test)

print(classification_report(y_test, preds_y_test_inverse))

Predictions:   [22, 26, 24, 8, 0]
                            precision    recall  f1-score   support

   Blister and Insert Card       0.73      0.45      0.56      1749
  Blister and sealed blist       0.73      0.65      0.69      1582
            Book packaging       0.54      1.00      0.70        20
Cardb. Sleeve w - w/o Shr.       0.18      0.64      0.28       135
  Cardboard hanger w/o bag       0.15      0.82      0.25        80
    Carton cover (Lid box)       0.28      0.80      0.41       130
   Carton tube with or w/o       0.10      1.00      0.18        20
                      Case       0.14      0.68      0.24        97
         Corrugated carton       0.79      0.60      0.69       774
        Countertop display       0.09      0.63      0.16        30
                  Envelope       0.43      0.88      0.58        59
          Fabric packaging       0.56      1.00      0.71        20
            Folding carton       0.90      0.33      0.49      1644
             